In [64]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from pandas_datareader import data as pdr
import plotly.express as px
import plotly.graph_objects as go
from scipy import stats
import plotly.figure_factory as ff
from sklearn.preprocessing import MinMaxScaler 
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score
from tensorflow import keras
from keras.callbacks import EarlyStopping
%config InlineBackend.figure_format = 'png'
%matplotlib inline

In [36]:
# read data for yahoo stock data
stock = 'AAPL'
start = '2000-01-01' 
end = '2020-12-01'
Data = pdr.get_data_yahoo(stock, start, end)
Data = Data.sort_values(by = ['Date'])

In [37]:
# Display first 5 rows and data shape
display(Data.head())
display(Data.shape)

High       Low      Open     Close       Volume  Adj Close
Date                                                                      
2000-01-03  1.004464  0.907924  0.936384  0.999442  535796800.0   0.855168
2000-01-04  0.987723  0.903460  0.966518  0.915179  512377600.0   0.783068
2000-01-05  0.987165  0.919643  0.926339  0.928571  778321600.0   0.794528
2000-01-06  0.955357  0.848214  0.947545  0.848214  767972800.0   0.725771
2000-01-07  0.901786  0.852679  0.861607  0.888393  460734400.0   0.760149

(5263, 6)

In [38]:
# Check for nan values
Data.isnull().sum()

High         0
Low          0
Open         0
Close        0
Volume       0
Adj Close    0
dtype: int64

In [39]:
# General stats for TESLA stock
Data.describe()

High          Low         Open        Close        Volume  \
count  5263.000000  5263.000000  5263.000000  5263.000000  5.263000e+03   
mean     18.483761    18.091581    18.288782    18.294883  4.461918e+08   
std      23.125953    22.571547    22.849964    22.860386  3.917890e+08   
min       0.235536     0.227143     0.231964     0.234286  2.019780e+07   
25%       1.361607     1.327857     1.343929     1.344286  1.781824e+08   
50%       9.219286     8.921785     9.110357     9.065000  3.341184e+08   
75%      27.758750    27.191251    27.478749    27.441251  5.936350e+08   
max     137.979996   130.529999   137.589996   134.179993  7.421641e+09   

         Adj Close  
count  5263.000000  
mean     17.163891  
std      22.547481  
min       0.200465  
25%       1.150232  
50%       7.756426  
75%      25.310430  
max     133.948898

In [40]:
# Return Data columns
Data.columns

Index(['High', 'Low', 'Open', 'Close', 'Volume', 'Adj Close'], dtype='object')

In [41]:
# Function to normalize stock prices based on their initial price
def normalize(df):
  x = df.copy()
  for i in x.columns:
    x[i] = x[i]/x[i][0]
  return x

In [42]:
# Function to plot interactive plots using Plotly Express
def interactive_plot(df, title):
  fig = px.line(title = title)
  for i in df.columns:
    fig.add_scatter(x = df.index, y = df[i], name = i)
  fig.show()

In [43]:
# plot interactive chart for stocks data before normalization
interactive_plot(normalize(Data.drop(columns=['Volume'])), 'TESLA stock prices normalized')
interactive_plot(normalize(Data[['Volume']]), 'TESLA stock volume normalized')

In [44]:
# Function to return the input/output (target) data for AI/ML Model
# Note that our goal is to predict the future stock price 
# Target stock price today will be tomorrow's price 
def training_window(data,look_back):
    df = data.copy()
    for i in range(1,look_back+1):
        df['Close(J-'+str(i)+')'] = df['Close'].shift(i)
    df['Target'] = df[['Close']].shift(-1)
    df = df[look_back:-1]
    return df

In [45]:
look_back = 6
Supervised_data = training_window(Data[['Volume','Close']], look_back)
Supervised_data

Volume       Close  Close(J-1)  Close(J-2)  Close(J-3)  \
Date                                                                       
2000-01-11  4.415488e+08    0.828125    0.872768    0.888393    0.848214   
2000-01-12  9.760688e+08    0.778460    0.828125    0.872768    0.888393   
2000-01-13  1.032685e+09    0.863839    0.778460    0.828125    0.872768   
2000-01-14  3.903760e+08    0.896763    0.863839    0.778460    0.828125   
2000-01-18  4.591776e+08    0.928013    0.896763    0.863839    0.778460   
...                  ...         ...         ...         ...         ...   
2020-11-23  1.279593e+08  113.849998  117.339996  118.639999  118.029999   
2020-11-24  1.138742e+08  115.169998  113.849998  117.339996  118.639999   
2020-11-25  7.649920e+07  116.029999  115.169998  113.849998  117.339996   
2020-11-27  4.669130e+07  116.589996  116.029999  115.169998  113.849998   
2020-11-30  1.694102e+08  119.050003  116.589996  116.029999  115.169998   

            Close(J-4)  Close(J-5)  Close(J-6)      Target  
Date                                                        
2000-01-11    0.928571    0.915179    0.999442    0.778460  
2000-01-12    0.848214    0.928571    0.915179    0.863839  
2000-01-13    0.888393    0.848214    0.928571    0.896763  
2000-01-14    0.872768    0.888393    0.848214    0.928013  
2000-01-18    0.828125    0.872768    0.888393    0.951451  
...                ...         ...         ...         ...  
2020-11-23  119.389999  120.300003  119.260002  115.169998  
2020-11-24  118.029999  119.389999  120.300003  116.029999  
2020-11-25  118.639999  118.029999  119.389999  116.589996  
2020-11-27  117.339996  118.639999  118.029999  119.050003  
2020-11-30  113.849998  117.339996  118.639999  122.720001  

[5256 rows x 9 columns]

In [46]:
# Tarin test split
frac_train = 0.7
Split = int(frac_train*Supervised_data.shape[0])
train_df = Supervised_data[:Split]
test_df = Supervised_data[Split:]
display(train_df)
display(test_df)

Volume      Close  Close(J-1)  Close(J-2)  Close(J-3)  \
Date                                                                      
2000-01-11  4.415488e+08   0.828125    0.872768    0.888393    0.848214   
2000-01-12  9.760688e+08   0.778460    0.828125    0.872768    0.888393   
2000-01-13  1.032685e+09   0.863839    0.778460    0.828125    0.872768   
2000-01-14  3.903760e+08   0.896763    0.863839    0.778460    0.828125   
2000-01-18  4.591776e+08   0.928013    0.896763    0.863839    0.778460   
...                  ...        ...         ...         ...         ...   
2014-08-20  2.107960e+08  25.142500   25.132500   24.790001   24.495001   
2014-08-21  1.339120e+08  25.145000   25.142500   25.132500   24.790001   
2014-08-22  1.767360e+08  25.330000   25.145000   25.142500   25.132500   
2014-08-25  1.610800e+08  25.385000   25.330000   25.145000   25.142500   
2014-08-26  1.326080e+08  25.222500   25.385000   25.330000   25.145000   

            Close(J-4)  Close(J-5)  Close(J-6)     Target  
Date                                                       
2000-01-11    0.928571    0.915179    0.999442   0.778460  
2000-01-12    0.848214    0.928571    0.915179   0.863839  
2000-01-13    0.888393    0.848214    0.928571   0.896763  
2000-01-14    0.872768    0.888393    0.848214   0.928013  
2000-01-18    0.828125    0.872768    0.888393   0.951451  
...                ...         ...         ...        ...  
2014-08-20   24.375000   24.309999   23.992500  25.145000  
2014-08-21   24.495001   24.375000   24.309999  25.330000  
2014-08-22   24.790001   24.495001   24.375000  25.385000  
2014-08-25   25.132500   24.790001   24.495001  25.222500  
2014-08-26   25.142500   25.132500   24.790001  25.532499  

[3679 rows x 9 columns]

Volume       Close  Close(J-1)  Close(J-2)  Close(J-3)  \
Date                                                                      
2014-08-27  209476000.0   25.532499   25.222500   25.385000   25.330000   
2014-08-28  273840000.0   25.562500   25.532499   25.222500   25.385000   
2014-08-29  178380000.0   25.625000   25.562500   25.532499   25.222500   
2014-09-02  214256000.0   25.825001   25.625000   25.562500   25.532499   
2014-09-03  501684000.0   24.735001   25.825001   25.625000   25.562500   
...                 ...         ...         ...         ...         ...   
2020-11-23  127959300.0  113.849998  117.339996  118.639999  118.029999   
2020-11-24  113874200.0  115.169998  113.849998  117.339996  118.639999   
2020-11-25   76499200.0  116.029999  115.169998  113.849998  117.339996   
2020-11-27   46691300.0  116.589996  116.029999  115.169998  113.849998   
2020-11-30  169410200.0  119.050003  116.589996  116.029999  115.169998   

            Close(J-4)  Close(J-5)  Close(J-6)      Target  
Date                                                        
2014-08-27   25.145000   25.142500   25.132500   25.562500  
2014-08-28   25.330000   25.145000   25.142500   25.625000  
2014-08-29   25.385000   25.330000   25.145000   25.825001  
2014-09-02   25.222500   25.385000   25.330000   24.735001  
2014-09-03   25.532499   25.222500   25.385000   24.530001  
...                ...         ...         ...         ...  
2020-11-23  119.389999  120.300003  119.260002  115.169998  
2020-11-24  118.029999  119.389999  120.300003  116.029999  
2020-11-25  118.639999  118.029999  119.389999  116.589996  
2020-11-27  117.339996  118.639999  118.029999  119.050003  
2020-11-30  113.849998  117.339996  118.639999  122.720001  

[1577 rows x 9 columns]

In [47]:
# Scale the data and divide it into variable X and traget y
# Note that we will devide data into train and test before scaling to avoid data linkage
sc = MinMaxScaler(feature_range=(0,1))
train = sc.fit_transform(train_df)
test = sc.fit_transform(test_df)
X_train = train[:,:-1]
y_train = train[:,-1:]
X_test = test[:,:-1]
y_test = test[:,-1:]
print('X train shape is {} and y train shape is {}'.format(X_train.shape,y_train.shape))
print('X test shape is {} and y test shape is {}'.format(X_test.shape,y_test.shape))

X train shape is (3679, 8) and y train shape is (3679, 1)
X test shape is (1577, 8) and y test shape is (1577, 1)


In [48]:
# Plot train data and test data without normalization 
fig = px.line(title = 'train and test data without normalization')
fig.add_scatter(x = Data.index[:Split], y = train_df['Close'],mode='lines', name = 'Close price train data')
fig.add_scatter(x = Data.index[Split:], y = test_df['Close'],mode='lines', name = 'Close price test data')
fig.show()
# Plot train data and test data normalized 
fig = px.line(title = 'train and test data normalized')
fig.add_scatter(x = Data.index[:Split], y = y_train[:,0],mode='lines', name = 'Target train data')
fig.add_scatter(x = Data.index[Split:], y = y_test[:,0],mode='lines', name = 'Target test data')
fig.show()

In [49]:
# Reshape the 1D arrays to 3D arrays to feed in the model
X_train = np.reshape(X_train, (X_train.shape[0], X_train.shape[1], 1))
X_test = np.reshape(X_test, (X_test.shape[0], X_test.shape[1], 1))
X_train.shape, X_test.shape

((3679, 8, 1), (1577, 8, 1))

In [50]:
from keras.regularizers import l2
# Create the model
inputs = keras.layers.Input(shape = (X_train.shape[1], X_train.shape[2]))
x = keras.layers.LSTM(150, return_sequences=True, recurrent_regularizer=l2(0.01), bias_regularizer=l2(0.001))(inputs)
x = keras.layers.Dropout(0.3)(x)
x = keras.layers.LSTM(150)(x)
x = keras.layers.Dropout(0.3)(x)
x = keras.layers.Dense(150, activation = 'relu')(x)
outputs = keras.layers.Dense(1, activation = 'linear')(x)

model = keras.Model(inputs=inputs, outputs= outputs)
model.compile(optimizer = 'adam', loss='mse')
model.summary()

Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         [(None, 8, 1)]            0         
_________________________________________________________________
lstm_4 (LSTM)                (None, 8, 150)            91200     
_________________________________________________________________
dropout_4 (Dropout)          (None, 8, 150)            0         
_________________________________________________________________
lstm_5 (LSTM)                (None, 150)               180600    
_________________________________________________________________
dropout_5 (Dropout)          (None, 150)               0         
_________________________________________________________________
dense_3 (Dense)              (None, 150)               22650     
_________________________________________________________________
dense_4 (Dense)              (None, 1)                 151 

In [51]:
# Train the model and save validation loss split in train
n_epochs = 100
es = EarlyStopping(monitor='val_loss', mode='min', verbose=1)
history = model.fit(X_train, y_train, epochs=n_epochs, batch_size=32, validation_split=0.2)

Train on 2943 samples, validate on 736 samples
Epoch 1/100
2943/2943 [==============================] - 4s 1ms/sample - loss: 0.5339 - val_loss: 0.1604
Epoch 2/100
2943/2943 [==============================] - 3s 853us/sample - loss: 0.1224 - val_loss: 0.1032
Epoch 3/100
2943/2943 [==============================] - 3s 899us/sample - loss: 0.0924 - val_loss: 0.0836
Epoch 4/100
2943/2943 [==============================] - 2s 836us/sample - loss: 0.0743 - val_loss: 0.0667
Epoch 5/100
2943/2943 [==============================] - 2s 785us/sample - loss: 0.0593 - val_loss: 0.0536
Epoch 6/100
2943/2943 [==============================] - 2s 830us/sample - loss: 0.0468 - val_loss: 0.0417
Epoch 7/100
2943/2943 [==============================] - 3s 882us/sample - loss: 0.0364 - val_loss: 0.0323
Epoch 8/100
2943/2943 [==============================] - 3s 959us/sample - loss: 0.0279 - val_loss: 0.0254
Epoch 9/100
2943/2943 [==============================] - 2s 821us/sample - loss: 0.0211 - val_loss:

2943/2943 [==============================] - 3s 985us/sample - loss: 1.3031e-04 - val_loss: 0.0026
Epoch 75/100
2943/2943 [==============================] - 3s 969us/sample - loss: 1.3856e-04 - val_loss: 0.0026
Epoch 76/100
2943/2943 [==============================] - 3s 988us/sample - loss: 1.2673e-04 - val_loss: 0.0016
Epoch 77/100
2943/2943 [==============================] - 3s 990us/sample - loss: 1.2571e-04 - val_loss: 4.9227e-04
Epoch 78/100
2943/2943 [==============================] - 3s 1ms/sample - loss: 1.5389e-04 - val_loss: 0.0049
Epoch 79/100
2943/2943 [==============================] - 3s 1ms/sample - loss: 1.1244e-04 - val_loss: 0.0027
Epoch 80/100
2943/2943 [==============================] - 3s 988us/sample - loss: 1.3948e-04 - val_loss: 0.0030
Epoch 81/100
2943/2943 [==============================] - 3s 1ms/sample - loss: 1.2412e-04 - val_loss: 0.0050
Epoch 82/100
2943/2943 [==============================] - 3s 1ms/sample - loss: 1.2557e-04 - val_loss: 0.0022
Epoch 83/

In [52]:
# Plot Model Loss progress During Training'
interactive_plot(pd.DataFrame(history.history), 'Model Loss progress During Training')

In [96]:
# Train the model with validation_data
n_epochs = 70
history = model.fit(X_train, y_train, epochs=n_epochs, batch_size=32, validation_data=(X_test,y_test))

Train on 1835 samples, validate on 787 samples
Epoch 1/150
1835/1835 [==============================] - 2s 933us/sample - loss: 9.8089e-04 - val_loss: 0.0014
Epoch 2/150
1835/1835 [==============================] - 2s 907us/sample - loss: 8.2652e-04 - val_loss: 7.2377e-04
Epoch 3/150
1835/1835 [==============================] - 2s 890us/sample - loss: 7.4622e-04 - val_loss: 7.4542e-04
Epoch 4/150
1835/1835 [==============================] - 2s 872us/sample - loss: 7.0390e-04 - val_loss: 7.9395e-04
Epoch 5/150
1835/1835 [==============================] - 2s 887us/sample - loss: 7.6950e-04 - val_loss: 9.9861e-04
Epoch 6/150
1835/1835 [==============================] - 2s 870us/sample - loss: 7.5025e-04 - val_loss: 7.4572e-04
Epoch 7/150
1835/1835 [==============================] - 2s 888us/sample - loss: 8.3099e-04 - val_loss: 9.6667e-04
Epoch 8/150
1835/1835 [==============================] - 2s 918us/sample - loss: 0.0010 - val_loss: 0.0016
Epoch 9/150
1835/1835 [======================

1835/1835 [==============================] - 2s 908us/sample - loss: 6.4778e-04 - val_loss: 6.2580e-04
Epoch 144/150
1835/1835 [==============================] - 2s 959us/sample - loss: 7.6845e-04 - val_loss: 8.6549e-04
Epoch 145/150
1835/1835 [==============================] - 2s 929us/sample - loss: 6.0137e-04 - val_loss: 9.0191e-04
Epoch 146/150
1835/1835 [==============================] - 2s 887us/sample - loss: 6.0727e-04 - val_loss: 6.8483e-04
Epoch 147/150
1835/1835 [==============================] - 2s 919us/sample - loss: 7.5120e-04 - val_loss: 8.3439e-04
Epoch 148/150
1835/1835 [==============================] - 2s 901us/sample - loss: 6.6351e-04 - val_loss: 7.2892e-04
Epoch 149/150
1835/1835 [==============================] - 2s 912us/sample - loss: 7.6398e-04 - val_loss: 8.4029e-04
Epoch 150/150
1835/1835 [==============================] - 2s 929us/sample - loss: 6.7133e-04 - val_loss: 7.9658e-04


In [151]:
# Plot Model Loss progress During Training'
interactive_plot(pd.DataFrame(history.history), 'Model Loss progress During Training')

In [56]:
# from the loss plot we can see that the validation loss is less volatile between 60 and 80
# we'll choose 70 epochs for training
# Train the model with validation_data
n_epochs = 2
es = EarlyStopping(monitor='val_loss', mode='min', verbose=1)
model.fit(X_train, y_train, epochs=n_epochs, batch_size=32, validation_data=(X_test,y_test))

Train on 3679 samples, validate on 1577 samples
Epoch 1/2
3679/3679 [==============================] - 3s 886us/sample - loss: 5.2952e-04 - val_loss: 2.7372e-04
Epoch 2/2
3679/3679 [==============================] - 3s 889us/sample - loss: 4.3043e-04 - val_loss: 2.6153e-04


In [99]:
# Inverse scale predictions and add predictions to supervised data 
#test_df = test_df.drop(columns=['Target'])
predictions = model.predict(X_test)
Predictions_df = pd.DataFrame(X_test[:,:,0], columns = test_df.columns[:-1], index=test_df.index)
Predictions_df['Predictions'] = predictions
Predictions_df = pd.DataFrame(sc.inverse_transform(Predictions_df),columns=Predictions_df.columns, index=Predictions_df.index)
Predictions_df['Target'] = test_df['Target']
Predictions_df = Predictions_df[['Target','Predictions']]
Predictions_df

Target  Predictions
Date                               
2014-08-27   25.562500    24.060930
2014-08-28   25.625000    24.230775
2014-08-29   25.825001    24.128065
2014-09-02   24.735001    24.304878
2014-09-03   24.530001    24.559768
...                ...          ...
2020-11-23  115.169998   116.950944
2020-11-24  116.029999   115.938966
2020-11-25  116.589996   115.362759
2020-11-27  119.050003   115.367549
2020-11-30  122.720001   116.559871

[1577 rows x 2 columns]

In [86]:
# Plot predictions over time
fig = px.line(title = 'Real Target vs predicted '+ stock + ' stock price over time')
fig.add_scatter(x = Supervised_data.index, y = Supervised_data['Target'],mode='lines', name = 'Real Target Close Price')
fig.add_scatter(x = Predictions_df.index, y = Predictions_df['Predictions'],mode='lines', name = 'Predicted Close Price')
fig.show()

In [100]:
# Plot predictions vs target
fig = px.scatter(title = 'Real Target vs predicted '+ stock + ' stock price')
fig.add_trace(go.Scatter(x = Predictions_df['Predictions'], y = Predictions_df['Target'],mode = 'markers'))
fig.show()

In [101]:
from sklearn.metrics import r2_score, mean_squared_error, mean_absolute_error
R2_score = r2_score(Predictions_df['Predictions'],Predictions_df['Target'])
MSE = mean_squared_error(Predictions_df['Predictions'],Predictions_df['Target'])
RMSE = MSE**(1/2)
MAE = mean_absolute_error(Predictions_df['Predictions'],Predictions_df['Target'])
print('R2_score is {}'.format(R2_score))
print('-'*50)
print('The mean squared error is {}'.format(MSE))
print('-'*50)
print('The root mean squared error is {}'.format(RMSE))
print('-'*50)
print('the mean absolute error is {}'.format(MAE))
print('-'*50)

R2_score is 0.9949189093055779
--------------------------------------------------
The mean squared error is 2.7621566088822846
--------------------------------------------------
The root mean squared error is 1.6619737088420756
--------------------------------------------------
the mean absolute error is 1.1701129820827723
--------------------------------------------------
